In [2]:
######### Jade Zhang
######### MIS5573
######### Final Project

In [90]:
import pandas as pd
import numpy as np
from statsmodels.tsa.stattools import adfuller
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.arima_model import ARIMA
from pmdarima.arima import auto_arima
from math import sqrt
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import LabelEncoder

import math

###### data cleaning

In [147]:
# import the dataset
close_prices = pd.read_csv('close_prices.csv')

In [148]:
close_prices

Symbol  closeDay0_y  closeDay1  closeDay2  closeDay3  closeDay4  \
0         A      28.6358    27.2040    29.3517    27.1198    27.6676   
1       AAC      18.5000    18.6500    19.2400    19.2400    19.1300   
2      AAOI       9.9600    10.1000    10.0000    10.0000     9.9700   
3       AAP      13.9000    14.2834    13.7830    13.2330    14.6670   
4       AAT      21.2500    21.3100    21.3100    21.3700    21.2500   
...     ...          ...        ...        ...        ...        ...   
3757   ZUMZ      12.4350    12.2550    12.0500    12.1250    11.7500   
3758    ZUO      20.0000    20.6000    20.6000    19.5500    19.5600   
3759     ZX       5.8500     6.2500     6.3000     6.0400     6.0800   
3760   ZYME      13.0000    13.0700    13.1000    13.2800    13.1100   
3761   ZYNE      16.2500    19.3200    24.5400    35.1400    29.7300   

      closeDay5  closeDay6  closeDay7  closeDay8  ...  closeDay252  \
0       27.6676    27.7518    28.3831    28.4256  ...      31.2467   
1       19.2500    19.0000    19.0000    18.1000  ...      23.5500   
2       10.0000    10.2000    10.1800    10.1200  ...      17.8800   
3       14.5730    14.6670    14.6170    14.5870  ...      17.4670   
4       21.2100    21.2500    21.3000    21.2700  ...      20.5100   
...         ...        ...        ...        ...  ...          ...   
3757    11.5600    11.5810    12.4150    12.5600  ...      32.4600   
3758    19.6500    19.7200        NaN        NaN  ...          NaN   
3759     6.0500     6.0095     6.0300     6.0000  ...       3.7100   
3760    13.0500    13.0300    13.0000    13.0900  ...      12.5000   
3761    32.0500    36.4900    34.8400    34.1100  ...       7.3200   

      closeDay253  closeDay254  closeDay255  closeDay256  closeDay257  \
0         30.9523      29.8992       29.352      26.5302      26.4885   
1         23.1500      24.1900       24.680      25.4400      23.4000   
2         17.8700      18.0700       18.510      18.0800      17.1000   
3         17.6500      17.7670       18.147      17.9330      16.8200   
4         20.9200      20.2500       20.490      20.3700      19.9200   
...           ...          ...          ...          ...          ...   
3757      32.3300      32.3100       33.050      33.2100      34.2100   
3758          NaN          NaN          NaN          NaN          NaN   
3759       3.7100       3.7100        3.710       3.5900       3.4920   
3760      12.4545      12.0152       11.980          NaN          NaN   
3761       7.1800       7.2800        7.960       8.1900       8.8400   

      closeDay258  closeDay259  closeDay260  closeDay261  
0          28.720      29.2254      28.0462      31.9205  
1          23.470      22.2500      22.5900      24.4300  
2          17.100      17.7700      16.9600      16.8100  
3          16.627      17.3033      17.3033      17.1830  
4          20.300      20.7300      20.4300      20.6900  
...           ...          ...          ...          ...  
3757       32.880      35.2100      34.8200          NaN  
3758          NaN          NaN          NaN          NaN  
3759        3.520       3.5200       3.4700       3.4600  
3760          NaN          NaN          NaN          NaN  
3761        9.200       8.8000       9.4300      10.5000  

[3762 rows x 263 columns]

In [149]:
close_prices = close_prices.transpose()

In [150]:
close_prices = close_prices.rename(columns = close_prices.iloc[0])

In [151]:
close_prices

A    AAC   AAOI      AAP    AAT    AAV   AAWW   AAXJ  \
Symbol             A    AAC   AAOI      AAP    AAT    AAV   AAWW   AAXJ   
closeDay0_y  28.6358   18.5   9.96     13.9  21.25   8.08  16.75  49.77   
closeDay1     27.204  18.65   10.1  14.2834  21.31    8.1  16.75  49.77   
closeDay2    29.3517  19.24     10   13.783  21.31   8.02  16.75  50.13   
closeDay3    27.1198  19.24     10   13.233  21.37   7.88  16.75     49   
...              ...    ...    ...      ...    ...    ...    ...    ...   
closeDay257  26.4885   23.4   17.1    16.82  19.92  7.525   31.5  50.26   
closeDay258    28.72  23.47   17.1   16.627   20.3   7.46     31  49.71   
closeDay259  29.2254  22.25  17.77  17.3033  20.73   7.46   30.5   48.9   
closeDay260  28.0462  22.59  16.96  17.3033  20.43   7.52   30.6  49.51   
closeDay261  31.9205  24.43  16.81   17.183  20.69   7.53     31  50.11   

              ABAC    ABB  ...   ZOES     ZS   ZSAN    ZTO    ZTS    ZUMZ  \
Symbol        ABAC    ABB  ...   ZOES     ZS   ZSAN    ZTO    ZTS    ZUMZ   
closeDay0_y   21.4  24.06  ...  24.72     33  220.2  16.57  31.01  12.435   
closeDay1       17  23.22  ...   25.1   27.9    221  16.99  31.02  12.255   
closeDay2    16.96  23.22  ...   25.2  30.38    224  16.93  31.04   12.05   
closeDay3    16.08  23.22  ...  28.21  31.08  221.8     16  31.03  12.125   
...            ...    ...  ...    ...    ...    ...    ...    ...     ...   
closeDay257  11.48  30.75  ...  32.21    NaN   39.4  15.38  31.44   34.21   
closeDay258  11.28  30.75  ...  33.34    NaN   39.4  15.57  30.78   32.88   
closeDay259  10.64  30.75  ...  33.55    NaN     46  15.63  30.67   35.21   
closeDay260  11.24     30  ...  34.09    NaN   50.2  15.54  30.36   34.82   
closeDay261  11.76    NaN  ...    NaN    NaN   45.6  15.73    NaN     NaN   

               ZUO     ZX   ZYME   ZYNE  
Symbol         ZUO     ZX   ZYME   ZYNE  
closeDay0_y     20   5.85     13  16.25  
closeDay1     20.6   6.25  13.07  19.32  
closeDay2     20.6    6.3   13.1  24.54  
closeDay3    19.55   6.04  13.28  35.14  
...            ...    ...    ...    ...  
closeDay257    NaN  3.492    NaN   8.84  
closeDay258    NaN   3.52    NaN    9.2  
closeDay259    NaN   3.52    NaN    8.8  
closeDay260    NaN   3.47    NaN   9.43  
closeDay261    NaN   3.46    NaN   10.5  

[263 rows x 3762 columns]

In [152]:
close_prices = close_prices.drop(['Symbol'])

In [153]:
close_prices

A    AAC   AAOI      AAP    AAT    AAV   AAWW   AAXJ  \
closeDay0_y  28.6358   18.5   9.96     13.9  21.25   8.08  16.75  49.77   
closeDay1     27.204  18.65   10.1  14.2834  21.31    8.1  16.75  49.77   
closeDay2    29.3517  19.24     10   13.783  21.31   8.02  16.75  50.13   
closeDay3    27.1198  19.24     10   13.233  21.37   7.88  16.75     49   
closeDay4    27.6676  19.13   9.97   14.667  21.25   7.85  16.75  48.34   
...              ...    ...    ...      ...    ...    ...    ...    ...   
closeDay257  26.4885   23.4   17.1    16.82  19.92  7.525   31.5  50.26   
closeDay258    28.72  23.47   17.1   16.627   20.3   7.46     31  49.71   
closeDay259  29.2254  22.25  17.77  17.3033  20.73   7.46   30.5   48.9   
closeDay260  28.0462  22.59  16.96  17.3033  20.43   7.52   30.6  49.51   
closeDay261  31.9205  24.43  16.81   17.183  20.69   7.53     31  50.11   

              ABAC    ABB  ...   ZOES     ZS   ZSAN    ZTO    ZTS    ZUMZ  \
closeDay0_y   21.4  24.06  ...  24.72     33  220.2  16.57  31.01  12.435   
closeDay1       17  23.22  ...   25.1   27.9    221  16.99  31.02  12.255   
closeDay2    16.96  23.22  ...   25.2  30.38    224  16.93  31.04   12.05   
closeDay3    16.08  23.22  ...  28.21  31.08  221.8     16  31.03  12.125   
closeDay4    15.92  23.22  ...  27.89  29.83  221.8     16     32   11.75   
...            ...    ...  ...    ...    ...    ...    ...    ...     ...   
closeDay257  11.48  30.75  ...  32.21    NaN   39.4  15.38  31.44   34.21   
closeDay258  11.28  30.75  ...  33.34    NaN   39.4  15.57  30.78   32.88   
closeDay259  10.64  30.75  ...  33.55    NaN     46  15.63  30.67   35.21   
closeDay260  11.24     30  ...  34.09    NaN   50.2  15.54  30.36   34.82   
closeDay261  11.76    NaN  ...    NaN    NaN   45.6  15.73    NaN     NaN   

               ZUO     ZX   ZYME   ZYNE  
closeDay0_y     20   5.85     13  16.25  
closeDay1     20.6   6.25  13.07  19.32  
closeDay2     20.6    6.3   13.1  24.54  
closeDay3    19.55   6.04  13.28  35.14  
closeDay4    19.56   6.08  13.11  29.73  
...            ...    ...    ...    ...  
closeDay257    NaN  3.492    NaN   8.84  
closeDay258    NaN   3.52    NaN    9.2  
closeDay259    NaN   3.52    NaN    8.8  
closeDay260    NaN   3.47    NaN   9.43  
closeDay261    NaN   3.46    NaN   10.5  

[262 rows x 3762 columns]

In [156]:
# export the table
close_prices.to_csv(r'close_prices.csv')

### RUN IT FROM HERE

In [158]:
# re-import & make the date the index & convert the datatype to DATE
dateparse = lambda dates:pd.datetime.strptime(dates,'%m/%d/%Y')
close_prices = pd.read_csv('close_prices.csv', index_col = 'DATE', parse_dates = ['DATE'], date_parser = dateparse)

In [162]:
# check the data type of index
close_prices.index

DatetimeIndex(['2018-01-01', '2018-01-02', '2018-01-03', '2018-01-04',
               '2018-01-05', '2018-01-06', '2018-01-07', '2018-01-08',
               '2018-01-09', '2018-01-10',
               ...
               '2018-09-10', '2018-09-11', '2018-09-12', '2018-09-13',
               '2018-09-14', '2018-09-15', '2018-09-16', '2018-09-17',
               '2018-09-18', '2018-09-19'],
              dtype='datetime64[ns]', name='DATE', length=262, freq=None)

In [163]:
# delete the columns that have too many missing values
frac = len(close_prices) * 0.8
close_prices = close_prices.dropna(thresh=frac, axis=1)

In [164]:
# filling nan by the closest values
close_prices = close_prices.ffill(limit = None)
close_prices = close_prices.bfill(limit = None)
close_prices = close_prices.ffill(limit = None)

In [165]:
# check if there's any nan value
close_prices.isnull().values.sum()

0

In [166]:
len(close_prices.columns)

3568

In [167]:
len(close_prices)

262

##### Generate regression result for every stock

In [174]:
############### function for time series prediction ############
def autoarimafun (column):
    # take log
    logcolumn = np.log(column)
    # seperate train test sets
    train, test = logcolumn[:int(260)], logcolumn[int(261)]
    # run ARIMA model
    model_autoARIMA = auto_arima(train,
                      trace=True,
                      error_action='ignore',  
                      suppress_warnings=True,
                                seasonal = False)
    
    predict = model_autoARIMA.predict(n_periods = 1)
    # return the predicted price for the last day
    return predict[0]

In [169]:
## add three rows to the dataframe 
# 1. Up & Down
# 2. Predicted Value
# 3. predicted value - real real value

# initializeation
close_prices = close_prices.append(pd.Series(name='Trend'))
close_prices = close_prices.append(pd.Series(name='PredictValue'))
close_prices = close_prices.append(pd.Series(name='Error'))

In [170]:
close_prices

A    AAC   AAOI      AAP    AAT   AAV   AAWW  \
DATE                                                                      
2018-01-01 00:00:00  28.6358  18.50   9.96  13.9000  21.25  8.08  16.75   
2018-01-02 00:00:00  27.2040  18.65  10.10  14.2834  21.31  8.10  16.75   
2018-01-03 00:00:00  29.3517  19.24  10.00  13.7830  21.31  8.02  16.75   
2018-01-04 00:00:00  27.1198  19.24  10.00  13.2330  21.37  7.88  16.75   
2018-01-05 00:00:00  27.6676  19.13   9.97  14.6670  21.25  7.85  16.75   
...                      ...    ...    ...      ...    ...   ...    ...   
2018-09-18 00:00:00  28.0462  22.59  16.96  17.3033  20.43  7.52  30.60   
2018-09-19 00:00:00  31.9205  24.43  16.81  17.1830  20.69  7.53  31.00   
Trend                    NaN    NaN    NaN      NaN    NaN   NaN    NaN   
PredictValue             NaN    NaN    NaN      NaN    NaN   NaN    NaN   
Error                    NaN    NaN    NaN      NaN    NaN   NaN    NaN   

                      AAXJ   ABAC    ABB  ...  ZNGA      ZNH   ZOES   ZSAN  \
DATE                                      ...                                
2018-01-01 00:00:00  49.77  21.40  24.06  ...  9.50  21.0000  24.72  220.2   
2018-01-02 00:00:00  49.77  17.00  23.22  ...  9.05  20.6667  25.10  221.0   
2018-01-03 00:00:00  50.13  16.96  23.22  ...  9.24  20.5000  25.20  224.0   
2018-01-04 00:00:00  49.00  16.08  23.22  ...  9.47  20.5000  28.21  221.8   
2018-01-05 00:00:00  48.34  15.92  23.22  ...  9.47  20.3753  27.89  221.8   
...                    ...    ...    ...  ...   ...      ...    ...    ...   
2018-09-18 00:00:00  49.51  11.24  30.00  ...  2.54   3.7920  34.09   50.2   
2018-09-19 00:00:00  50.11  11.76  30.00  ...  2.54   3.9587  34.09   45.6   
Trend                  NaN    NaN    NaN  ...   NaN      NaN    NaN    NaN   
PredictValue           NaN    NaN    NaN  ...   NaN      NaN    NaN    NaN   
Error                  NaN    NaN    NaN  ...   NaN      NaN    NaN    NaN   

                       ZTO    ZTS    ZUMZ    ZX   ZYME   ZYNE  
DATE                                                           
2018-01-01 00:00:00  16.57  31.01  12.435  5.85  13.00  16.25  
2018-01-02 00:00:00  16.99  31.02  12.255  6.25  13.07  19.32  
2018-01-03 00:00:00  16.93  31.04  12.050  6.30  13.10  24.54  
2018-01-04 00:00:00  16.00  31.03  12.125  6.04  13.28  35.14  
2018-01-05 00:00:00  16.00  32.00  11.750  6.08  13.11  29.73  
...                    ...    ...     ...   ...    ...    ...  
2018-09-18 00:00:00  15.54  30.36  34.820  3.47  11.98   9.43  
2018-09-19 00:00:00  15.73  30.36  34.820  3.46  11.98  10.50  
Trend                  NaN    NaN     NaN   NaN    NaN    NaN  
PredictValue           NaN    NaN     NaN   NaN    NaN    NaN  
Error                  NaN    NaN     NaN   NaN    NaN    NaN  

[265 rows x 3568 columns]

In [171]:
# set the trend row
for column in close_prices.columns[0:]:
    if (close_prices[column][261] - close_prices[column][260]) >= 0:
        close_prices[column][262] = 1   # 1 = UP
    else:
        close_prices[column][262] = 0   # 2 = Down

In [173]:
close_prices

A    AAC   AAOI      AAP    AAT   AAV   AAWW  \
DATE                                                                      
2018-01-01 00:00:00  28.6358  18.50   9.96  13.9000  21.25  8.08  16.75   
2018-01-02 00:00:00  27.2040  18.65  10.10  14.2834  21.31  8.10  16.75   
2018-01-03 00:00:00  29.3517  19.24  10.00  13.7830  21.31  8.02  16.75   
2018-01-04 00:00:00  27.1198  19.24  10.00  13.2330  21.37  7.88  16.75   
2018-01-05 00:00:00  27.6676  19.13   9.97  14.6670  21.25  7.85  16.75   
...                      ...    ...    ...      ...    ...   ...    ...   
2018-09-18 00:00:00  28.0462  22.59  16.96  17.3033  20.43  7.52  30.60   
2018-09-19 00:00:00  31.9205  24.43  16.81  17.1830  20.69  7.53  31.00   
Trend                 1.0000   1.00   0.00   0.0000   1.00  1.00   1.00   
PredictValue             NaN    NaN    NaN      NaN    NaN   NaN    NaN   
Error                    NaN    NaN    NaN      NaN    NaN   NaN    NaN   

                      AAXJ   ABAC    ABB  ...  ZNGA      ZNH   ZOES   ZSAN  \
DATE                                      ...                                
2018-01-01 00:00:00  49.77  21.40  24.06  ...  9.50  21.0000  24.72  220.2   
2018-01-02 00:00:00  49.77  17.00  23.22  ...  9.05  20.6667  25.10  221.0   
2018-01-03 00:00:00  50.13  16.96  23.22  ...  9.24  20.5000  25.20  224.0   
2018-01-04 00:00:00  49.00  16.08  23.22  ...  9.47  20.5000  28.21  221.8   
2018-01-05 00:00:00  48.34  15.92  23.22  ...  9.47  20.3753  27.89  221.8   
...                    ...    ...    ...  ...   ...      ...    ...    ...   
2018-09-18 00:00:00  49.51  11.24  30.00  ...  2.54   3.7920  34.09   50.2   
2018-09-19 00:00:00  50.11  11.76  30.00  ...  2.54   3.9587  34.09   45.6   
Trend                 1.00   1.00   1.00  ...  1.00   1.0000   1.00    0.0   
PredictValue           NaN    NaN    NaN  ...   NaN      NaN    NaN    NaN   
Error                  NaN    NaN    NaN  ...   NaN      NaN    NaN    NaN   

                       ZTO    ZTS    ZUMZ    ZX   ZYME   ZYNE  
DATE                                                           
2018-01-01 00:00:00  16.57  31.01  12.435  5.85  13.00  16.25  
2018-01-02 00:00:00  16.99  31.02  12.255  6.25  13.07  19.32  
2018-01-03 00:00:00  16.93  31.04  12.050  6.30  13.10  24.54  
2018-01-04 00:00:00  16.00  31.03  12.125  6.04  13.28  35.14  
2018-01-05 00:00:00  16.00  32.00  11.750  6.08  13.11  29.73  
...                    ...    ...     ...   ...    ...    ...  
2018-09-18 00:00:00  15.54  30.36  34.820  3.47  11.98   9.43  
2018-09-19 00:00:00  15.73  30.36  34.820  3.46  11.98  10.50  
Trend                 1.00   1.00   1.000  0.00   1.00   1.00  
PredictValue           NaN    NaN     NaN   NaN    NaN    NaN  
Error                  NaN    NaN     NaN   NaN    NaN    NaN  

[265 rows x 3568 columns]

In [175]:
# set the predict value and the error row
for column in close_prices.columns[0:500]:
    prediction = autoarimafun(close_prices[column])
    prediction = math.exp(float(prediction))
    close_prices[column][263] = prediction 
    close_prices[column][264] = prediction - close_prices[column][261]


Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-665.422, BIC=-644.081, Time=0.407 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-668.759, BIC=-661.645, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-667.764, BIC=-657.093, Time=0.040 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-667.706, BIC=-657.036, Time=0.060 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-670.759, BIC=-667.202, Time=0.023 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-665.989, BIC=-651.762, Time=0.172 seconds
Total fit time: 0.738 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-806.648, BIC=-785.307, Time=0.193 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-810.419, BIC=-803.305, Time=0.041 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-810.016, BIC=-799.345, Time=0.036 seconds
F

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-963.774, BIC=-942.433, Time=0.425 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-962.867, BIC=-955.753, Time=0.037 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-966.033, BIC=-955.362, Time=0.069 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-965.950, BIC=-955.280, Time=0.177 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-963.944, BIC=-960.388, Time=0.020 seconds
Fit ARIMA: (2, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-964.047, BIC=-949.820, Time=0.115 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-964.041, BIC=-949.814, Time=0.100 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-962.038, BIC=-944.254, Time=0.165 seconds
Total fit time: 1.110 seconds
Performing stepwise search to minimize aic


C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1164.603, BIC=-1143.262, Time=0.345 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1164.300, BIC=-1157.186, Time=0.035 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1166.600, BIC=-1155.930, Time=0.156 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1167.754, BIC=-1157.084, Time=0.150 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1166.012, BIC=-1162.455, Time=0.012 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1167.035, BIC=-1152.807, Time=0.104 seconds
Fit ARIMA: (0, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1167.840, BIC=-1153.613, Time=0.121 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1166.086, BIC=-1148.302, Time=0.184 seconds
Fit ARIMA: (0, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-1166.248, BIC=-1148.463, Time=0.163 seconds
Fit ARIMA: (1, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-1164.573, BIC=-1143.232, Time=0.233 seconds

...

Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1494.426, BIC=-1473.085, Time=0.278 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1501.804, BIC=-1494.690, Time=0.047 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1499.913, BIC=-1489.243, Time=0.036 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1499.924, BIC=-1489.253, Time=0.036 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1501.085, BIC=-1497.528, Time=0.015 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1500.328, BIC=-1486.100, Time=0.419 seconds
Total fit time: 0.836 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-298.679, BIC=-277.338, Time=0.177 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-293.372, BIC=-286.258, Time=0.037 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-303.774, BIC=-293.104, Time=0.052 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-909.317, BIC=-887.976, Time=0.358 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-903.694, BIC=-896.580, Time=0.037 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-902.317, BIC=-891.647, Time=0.096 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-902.705, BIC=-892.035, Time=0.096 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-905.210, BIC=-901.653, Time=0.043 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-911.333, BIC=-893.548, Time=0.260 seconds
Fit ARIMA: (0, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-911.069, BIC=-896.842, Time=0.169 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-904.042, BIC=-889.814, Time=0.204 seconds
Fit ARIMA: (1, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-909.193, BIC=-887.852, Time=0.406 seconds
Fit ARIMA: (0, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-911.251, BIC=-893.467, Time=0.191 seconds
Fit ARIMA: (2, 1, 1

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1043.392, BIC=-1022.051, Time=0.403 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1036.554, BIC=-1029.440, Time=0.065 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1044.833, BIC=-1034.162, Time=0.032 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1043.884, BIC=-1033.214, Time=0.067 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1037.860, BIC=-1034.303, Time=0.015 seconds
Fit ARIMA: (2, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1043.367, BIC=-1029.140, Time=0.105 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1043.286, BIC=-1029.059, Time=0.180 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1040.834, BIC=-1023.050, Time=0.160 seconds
Total fit time: 1.032 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1304.837, BIC=-1283.496, Time=0.177 seconds
Fit ARIMA: (0, 1, 0)x(0, 0

In [177]:
for column in close_prices.columns[500:1000]:
    prediction = autoarimafun(close_prices[column])
    prediction = math.exp(float(prediction))
    close_prices[column][263] = prediction 
    close_prices[column][264] = prediction - close_prices[column][261]


Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1260.231, BIC=-1238.890, Time=0.443 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1250.261, BIC=-1243.147, Time=0.043 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1252.721, BIC=-1242.050, Time=0.030 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1255.239, BIC=-1244.569, Time=0.069 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1251.037, BIC=-1247.480, Time=0.017 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1260.118, BIC=-1242.334, Time=0.335 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1260.417, BIC=-1242.633, Time=0.321 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1256.048, BIC=-1241.821, Time=0.226 seconds
Fit ARIMA: (2, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1258.239, BIC=-1244.012, Time=0.095 seconds
Fit ARIMA: (3, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1233.556, BIC=-1212.215, Time=0.419 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1234.844, BIC=-1227.731, Time=0.032 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1233.378, BIC=-1222.707, Time=0.141 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1233.343, BIC=-1222.672, Time=0.079 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1236.658, BIC=-1233.101, Time=0.011 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1231.358, BIC=-1217.131, Time=0.277 seconds
Total fit time: 0.962 seconds
Performing stepwise search to minimize aic


C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-871.859, BIC=-850.518, Time=0.272 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-878.091, BIC=-870.978, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-876.337, BIC=-865.666, Time=0.029 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-876.309, BIC=-865.639, Time=0.043 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-880.011, BIC=-876.454, Time=0.020 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-875.410, BIC=-861.183, Time=0.096 seconds
Total fit time: 0.496 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1542.447, BIC=-1521.106, Time=0.402 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1542.745, BIC=-1535.632, Time=0.060 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1542.962, BIC=-1532.292, Time=0.069 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (con

...

Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-2109.031, BIC=-2101.917, Time=0.038 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-2132.273, BIC=-2121.603, Time=0.057 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-2135.383, BIC=-2124.712, Time=0.056 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-2111.015, BIC=-2107.459, Time=0.019 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-2133.069, BIC=-2118.842, Time=0.210 seconds
Fit ARIMA: (0, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-2133.618, BIC=-2119.391, Time=0.111 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-2131.418, BIC=-2113.634, Time=0.181 seconds
Total fit time: 0.837 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1132.596, BIC=-1111.255, Time=0.375 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1135.169, BIC=-1128.055, Time=0.063 seconds
Fit ARIMA: (1, 1, 0)x(0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-784.397, BIC=-763.056, Time=0.423 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-787.418, BIC=-780.304, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-787.235, BIC=-776.564, Time=0.040 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-787.107, BIC=-776.436, Time=0.108 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-788.633, BIC=-785.077, Time=0.018 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-785.329, BIC=-771.101, Time=0.072 seconds
Total fit time: 0.697 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-566.679, BIC=-545.338, Time=0.279 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-573.547, BIC=-566.433, Time=0.056 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-571.608, BIC=-560.938, Time=0.032 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1180.167, BIC=-1158.826, Time=0.402 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1175.944, BIC=-1168.830, Time=0.036 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1179.767, BIC=-1169.097, Time=0.044 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1178.803, BIC=-1168.133, Time=0.078 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1177.480, BIC=-1173.923, Time=0.011 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1181.615, BIC=-1163.830, Time=0.351 seconds
Fit ARIMA: (0, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1178.985, BIC=-1164.757, Time=0.103 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1180.789, BIC=-1166.562, Time=0.114 seconds
Fit ARIMA: (1, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-1182.465, BIC=-1161.124, Time=0.400 seconds
Fit ARIMA: (0, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-1184.527, BIC=-1166.743, Time=0.224 seconds

In [179]:
for column in close_prices.columns[1000:2000]:
    prediction = autoarimafun(close_prices[column])
    prediction = math.exp(float(prediction))
    close_prices[column][263] = prediction 
    close_prices[column][264] = prediction - close_prices[column][261]

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-800.927, BIC=-779.586, Time=0.200 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-797.250, BIC=-790.136, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-796.689, BIC=-786.018, Time=0.036 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-797.440, BIC=-786.770, Time=0.069 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-799.153, BIC=-795.596, Time=0.043 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-802.513, BIC=-784.729, Time=0.261 seconds
Fit ARIMA: (0, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-803.885, BIC=-789.658, Time=0.121 seconds
Fit ARIMA: (0, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-802.205, BIC=-784.420, Time=0.138 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-802.706, BIC=-788.479, Time=0.200 seconds
Fit ARIMA: (1, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-800.170, BIC=-778.

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-482.771, BIC=-461.430, Time=0.286 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-476.819, BIC=-469.706, Time=0.037 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-484.662, BIC=-473.992, Time=0.054 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-483.552, BIC=-472.881, Time=0.060 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-478.817, BIC=-475.260, Time=0.014 seconds
Fit ARIMA: (2, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-482.988, BIC=-468.761, Time=0.068 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-482.832, BIC=-468.604, Time=0.173 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-481.361, BIC=-463.577, Time=0.235 seconds
Total fit time: 0.931 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-933.258, BIC=-911.917, Time=0.280 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


...

Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1441.501, BIC=-1420.161, Time=0.209 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1448.455, BIC=-1441.342, Time=0.057 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1446.968, BIC=-1436.298, Time=0.033 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1447.017, BIC=-1436.347, Time=0.148 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1449.946, BIC=-1446.389, Time=0.009 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1444.991, BIC=-1430.764, Time=0.149 seconds
Total fit time: 0.607 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-857.229, BIC=-835.889, Time=0.355 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-861.748, BIC=-854.634, Time=0.045 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-859.949, BIC=-849.278, Time=0.157 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1170.230, BIC=-1163.116, Time=0.053 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1169.628, BIC=-1158.957, Time=0.055 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1169.767, BIC=-1159.097, Time=0.075 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1172.071, BIC=-1168.514, Time=0.048 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1168.080, BIC=-1153.853, Time=0.099 seconds
Total fit time: 0.534 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1513.351, BIC=-1492.010, Time=0.237 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1520.094, BIC=-1512.980, Time=0.035 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1519.155, BIC=-1508.484, Time=0.074 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1519.094, BIC=-1508.424, Time=0.034 seconds
Fit ARIMA: (0, 1, 0)x(0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 0, 2)x(0, 0, 0, 0) (constant=True); AIC=-1191.362, BIC=-1169.998, Time=0.297 seconds
Fit ARIMA: (0, 0, 0)x(0, 0, 0, 0) (constant=True); AIC=-730.611, BIC=-723.489, Time=0.032 seconds
Fit ARIMA: (1, 0, 0)x(0, 0, 0, 0) (constant=True); AIC=-1187.361, BIC=-1176.679, Time=0.023 seconds
Fit ARIMA: (0, 0, 1)x(0, 0, 0, 0) (constant=True); AIC=-964.910, BIC=-954.228, Time=0.119 seconds
Fit ARIMA: (0, 0, 0)x(0, 0, 0, 0) (constant=False); AIC=1415.097, BIC=1418.658, Time=0.006 seconds
Fit ARIMA: (1, 0, 2)x(0, 0, 0, 0) (constant=True); AIC=-1190.719, BIC=-1172.916, Time=0.573 seconds
Fit ARIMA: (2, 0, 1)x(0, 0, 0, 0) (constant=True); AIC=-1186.554, BIC=-1168.751, Time=0.652 seconds
Fit ARIMA: (3, 0, 2)x(0, 0, 0, 0) (constant=True); AIC=-1189.371, BIC=-1164.446, Time=1.138 seconds
Fit ARIMA: (2, 0, 3)x(0, 0, 0, 0) (constant=True); AIC=-1190.612, BIC=-1165.688, Time=0.574 seconds
Fit ARIMA: (1, 0, 1)x(0, 0, 0, 0) (constant=True); AIC=-1185.982, BIC=-1171.739, Time=0.314 seconds
Fit A

In [180]:
for column in close_prices.columns[2000:3000]:
    prediction = autoarimafun(close_prices[column])
    prediction = math.exp(float(prediction))
    close_prices[column][263] = prediction 
    close_prices[column][264] = prediction - close_prices[column][261]

Performing stepwise search to minimize aic


C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1174.026, BIC=-1152.685, Time=0.532 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1179.480, BIC=-1172.366, Time=0.032 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1178.904, BIC=-1168.233, Time=0.187 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1178.948, BIC=-1168.278, Time=0.071 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1178.330, BIC=-1174.773, Time=0.012 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1176.959, BIC=-1162.732, Time=0.076 seconds
Total fit time: 0.913 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1177.150, BIC=-1155.809, Time=0.173 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1184.309, BIC=-1177.195, Time=0.051 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1182.310, BIC=-1171.639, Time=0.153 seconds
Fit ARIMA: (0, 1, 1)x(0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-643.846, BIC=-622.505, Time=0.371 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-645.718, BIC=-638.605, Time=0.038 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-645.038, BIC=-634.368, Time=0.174 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-645.255, BIC=-634.585, Time=0.056 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-647.173, BIC=-643.616, Time=0.014 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-641.720, BIC=-627.493, Time=0.100 seconds
Total fit time: 0.754 seconds
Performing stepwise search to minimize aic


...

Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1592.347, BIC=-1571.007, Time=0.350 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1592.920, BIC=-1585.807, Time=0.036 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1591.267, BIC=-1580.596, Time=0.056 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1591.292, BIC=-1580.621, Time=0.112 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1593.651, BIC=-1590.094, Time=0.018 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1588.992, BIC=-1574.764, Time=0.088 seconds
Total fit time: 0.662 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-511.574, BIC=-490.233, Time=0.331 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-513.649, BIC=-506.535, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-512.099, BIC=-501.428, Time=0.031 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1141.728, BIC=-1120.387, Time=0.194 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1148.981, BIC=-1141.867, Time=0.054 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1147.365, BIC=-1136.694, Time=0.037 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1147.335, BIC=-1136.664, Time=0.044 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1150.980, BIC=-1147.423, Time=0.014 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1145.499, BIC=-1131.271, Time=0.105 seconds
Total fit time: 0.449 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-864.563, BIC=-843.222, Time=0.319 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-866.740, BIC=-859.626, Time=0.030 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-866.102, BIC=-855.431, Time=0.056 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1367.688, BIC=-1346.347, Time=0.478 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1375.422, BIC=-1368.308, Time=0.035 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1373.844, BIC=-1363.174, Time=0.046 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1373.967, BIC=-1363.296, Time=0.098 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1376.152, BIC=-1372.596, Time=0.012 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1373.539, BIC=-1359.312, Time=0.226 seconds
Total fit time: 0.898 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-869.121, BIC=-847.780, Time=0.291 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-869.608, BIC=-862.494, Time=0.042 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-868.293, BIC=-857.622, Time=0.030 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0

In [181]:
for column in close_prices.columns[3000:]:
    prediction = autoarimafun(close_prices[column])
    prediction = math.exp(float(prediction))
    close_prices[column][263] = prediction 
    close_prices[column][264] = prediction - close_prices[column][261]

Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-623.946, BIC=-602.605, Time=0.362 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-618.126, BIC=-611.012, Time=0.044 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-616.993, BIC=-606.322, Time=0.028 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-616.870, BIC=-606.199, Time=0.056 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-616.035, BIC=-612.478, Time=0.016 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-614.948, BIC=-597.164, Time=0.201 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-614.695, BIC=-596.911, Time=0.074 seconds
Fit ARIMA: (3, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-622.076, BIC=-597.178, Time=0.438 seconds
Fit ARIMA: (2, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-614.170, BIC=-589.272, Time=0.445 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-615.664, BIC=-601.

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1151.557, BIC=-1130.216, Time=0.396 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1142.133, BIC=-1135.019, Time=0.031 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1145.127, BIC=-1134.457, Time=0.087 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1145.409, BIC=-1134.739, Time=0.076 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1144.119, BIC=-1140.562, Time=0.019 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1141.947, BIC=-1124.163, Time=0.246 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1143.257, BIC=-1125.472, Time=0.245 seconds
Fit ARIMA: (3, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1149.466, BIC=-1124.569, Time=0.409 seconds
Fit ARIMA: (2, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-1150.499, BIC=-1125.601, Time=0.414 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1362.274, BIC=-1340.933, Time=0.190 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1368.386, BIC=-1361.272, Time=0.034 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1367.722, BIC=-1357.052, Time=0.072 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1367.707, BIC=-1357.036, Time=0.066 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1366.162, BIC=-1362.606, Time=0.012 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1365.628, BIC=-1351.401, Time=0.067 seconds
Total fit time: 0.443 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1664.467, BIC=-1643.126, Time=0.176 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1652.018, BIC=-1644.904, Time=0.036 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1670.315, BIC=-1659.645, Time=0.154 seconds
Fit ARIMA: (0, 1, 1)x(0, 0

...

Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1064.023, BIC=-1042.682, Time=0.323 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1069.102, BIC=-1061.989, Time=0.031 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1067.304, BIC=-1056.633, Time=0.084 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1067.320, BIC=-1056.650, Time=0.066 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-1070.465, BIC=-1066.908, Time=0.019 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-1065.478, BIC=-1051.251, Time=0.084 seconds
Total fit time: 0.609 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 2, 2)x(0, 0, 0, 0) (constant=True); AIC=-1197.622, BIC=-1176.304, Time=0.271 seconds
Fit ARIMA: (0, 2, 0)x(0, 0, 0, 0) (constant=True); AIC=-1059.744, BIC=-1052.638, Time=0.057 seconds
Fit ARIMA: (1, 2, 0)x(0, 0, 0, 0) (constant=True); AIC=-1118.637, BIC=-1107.978, Time=0.090 seconds
Fit ARIMA: (0, 2, 1)x(0, 0

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-849.900, BIC=-842.787, Time=0.034 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-854.640, BIC=-843.969, Time=0.116 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-854.246, BIC=-843.575, Time=0.162 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-847.566, BIC=-844.009, Time=0.023 seconds
Fit ARIMA: (2, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-852.818, BIC=-838.590, Time=0.107 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-852.995, BIC=-838.768, Time=0.046 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-850.764, BIC=-832.980, Time=0.180 seconds
Total fit time: 0.845 seconds
Performing stepwise search to minimize aic
Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-1137.569, BIC=-1116.228, Time=0.240 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-1141.758, BIC=-1134.645, Time=0.039 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (const

C:\Users\Shuyu\.conda\envs\fullcombo\lib\site-packages\pandas\core\series.py:853: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


Fit ARIMA: (2, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-926.189, BIC=-904.848, Time=0.382 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-920.230, BIC=-913.116, Time=0.033 seconds
Fit ARIMA: (1, 1, 0)x(0, 0, 0, 0) (constant=True); AIC=-918.330, BIC=-907.659, Time=0.030 seconds
Fit ARIMA: (0, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-918.381, BIC=-907.710, Time=0.088 seconds
Fit ARIMA: (0, 1, 0)x(0, 0, 0, 0) (constant=False); AIC=-921.627, BIC=-918.070, Time=0.020 seconds
Fit ARIMA: (1, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-921.080, BIC=-903.296, Time=0.270 seconds
Fit ARIMA: (2, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-921.855, BIC=-904.071, Time=0.051 seconds
Fit ARIMA: (3, 1, 2)x(0, 0, 0, 0) (constant=True); AIC=-925.419, BIC=-900.522, Time=0.437 seconds
Fit ARIMA: (2, 1, 3)x(0, 0, 0, 0) (constant=True); AIC=-925.900, BIC=-901.002, Time=0.449 seconds
Fit ARIMA: (1, 1, 1)x(0, 0, 0, 0) (constant=True); AIC=-917.478, BIC=-903.250, Time=0.223 seconds
Fit ARIMA: (1, 1, 3

In [182]:
close_prices.merge()

A    AAC       AAOI        AAP        AAT  \
DATE                                                                   
2018-01-01 00:00:00  28.6358  18.50   9.960000  13.900000  21.250000   
2018-01-02 00:00:00  27.2040  18.65  10.100000  14.283400  21.310000   
2018-01-03 00:00:00  29.3517  19.24  10.000000  13.783000  21.310000   
2018-01-04 00:00:00  27.1198  19.24  10.000000  13.233000  21.370000   
2018-01-05 00:00:00  27.6676  19.13   9.970000  14.667000  21.250000   
...                      ...    ...        ...        ...        ...   
2018-09-18 00:00:00  28.0462  22.59  16.960000  17.303300  20.430000   
2018-09-19 00:00:00  31.9205  24.43  16.810000  17.183000  20.690000   
Trend                 1.0000   1.00   0.000000   0.000000   1.000000   
PredictValue         29.2254  22.25  17.901029  17.410343  20.705901   
Error                -2.6951  -2.18   1.091029   0.227343   0.015901   

                          AAV       AAWW       AAXJ   ABAC    ABB  ...  \
DATE                                                               ...   
2018-01-01 00:00:00  8.080000  16.750000  49.770000  21.40  24.06  ...   
2018-01-02 00:00:00  8.100000  16.750000  49.770000  17.00  23.22  ...   
2018-01-03 00:00:00  8.020000  16.750000  50.130000  16.96  23.22  ...   
2018-01-04 00:00:00  7.880000  16.750000  49.000000  16.08  23.22  ...   
2018-01-05 00:00:00  7.850000  16.750000  48.340000  15.92  23.22  ...   
...                       ...        ...        ...    ...    ...  ...   
2018-09-18 00:00:00  7.520000  30.600000  49.510000  11.24  30.00  ...   
2018-09-19 00:00:00  7.530000  31.000000  50.110000  11.76  30.00  ...   
Trend                1.000000   1.000000   1.000000   1.00   1.00  ...   
PredictValue         7.500456  30.570659  49.097035  10.64  30.75  ...   
Error               -0.029544  -0.429341  -1.012965  -1.12   0.75  ...   

                         ZNGA        ZNH   ZOES        ZSAN    ZTO       ZTS  \
DATE                                                                           
2018-01-01 00:00:00  9.500000  21.000000  24.72  220.200000  16.57  31.01000   
2018-01-02 00:00:00  9.050000  20.666700  25.10  221.000000  16.99  31.02000   
2018-01-03 00:00:00  9.240000  20.500000  25.20  224.000000  16.93  31.04000   
2018-01-04 00:00:00  9.470000  20.500000  28.21  221.800000  16.00  31.03000   
2018-01-05 00:00:00  9.470000  20.375300  27.89  221.800000  16.00  32.00000   
...                       ...        ...    ...         ...    ...       ...   
2018-09-18 00:00:00  2.540000   3.792000  34.09   50.200000  15.54  30.36000   
2018-09-19 00:00:00  2.540000   3.958700  34.09   45.600000  15.73  30.36000   
Trend                1.000000   1.000000   1.00    0.000000   1.00   1.00000   
PredictValue         2.607002   3.933278  33.55   46.948589  15.63  30.77699   
Error                0.067002  -0.025422  -0.54    1.348589  -0.10   0.41699   

                          ZUMZ        ZX   ZYME       ZYNE  
DATE                                                        
2018-01-01 00:00:00  12.435000  5.850000  13.00  16.250000  
2018-01-02 00:00:00  12.255000  6.250000  13.07  19.320000  
2018-01-03 00:00:00  12.050000  6.300000  13.10  24.540000  
2018-01-04 00:00:00  12.125000  6.040000  13.28  35.140000  
2018-01-05 00:00:00  11.750000  6.080000  13.11  29.730000  
...                        ...       ...    ...        ...  
2018-09-18 00:00:00  34.820000  3.470000  11.98   9.430000  
2018-09-19 00:00:00  34.820000  3.460000  11.98  10.500000  
Trend                 1.000000  0.000000   1.00   1.000000  
PredictValue         35.351779  3.505572  11.98   8.790237  
Error                 0.531779  0.045572   0.00  -1.709763  

[265 rows x 3568 columns]

In [ ]:
# add a new row for predicted trend
close_prices = close_prices.append(pd.Series(name='PredictedTrend'))

In [190]:
close_prices

A    AAC       AAOI        AAP        AAT  \
DATE                                                                   
2018-01-01 00:00:00  28.6358  18.50   9.960000  13.900000  21.250000   
2018-01-02 00:00:00  27.2040  18.65  10.100000  14.283400  21.310000   
2018-01-03 00:00:00  29.3517  19.24  10.000000  13.783000  21.310000   
2018-01-04 00:00:00  27.1198  19.24  10.000000  13.233000  21.370000   
2018-01-05 00:00:00  27.6676  19.13   9.970000  14.667000  21.250000   
...                      ...    ...        ...        ...        ...   
2018-09-19 00:00:00  31.9205  24.43  16.810000  17.183000  20.690000   
Trend                 1.0000   1.00   0.000000   0.000000   1.000000   
PredictValue         29.2254  22.25  17.901029  17.410343  20.705901   
Error                -2.6951  -2.18   1.091029   0.227343   0.015901   
PredictedTrend        1.0000   0.00   1.000000   1.000000   1.000000   

                          AAV       AAWW       AAXJ   ABAC    ABB  ...  \
DATE                                                               ...   
2018-01-01 00:00:00  8.080000  16.750000  49.770000  21.40  24.06  ...   
2018-01-02 00:00:00  8.100000  16.750000  49.770000  17.00  23.22  ...   
2018-01-03 00:00:00  8.020000  16.750000  50.130000  16.96  23.22  ...   
2018-01-04 00:00:00  7.880000  16.750000  49.000000  16.08  23.22  ...   
2018-01-05 00:00:00  7.850000  16.750000  48.340000  15.92  23.22  ...   
...                       ...        ...        ...    ...    ...  ...   
2018-09-19 00:00:00  7.530000  31.000000  50.110000  11.76  30.00  ...   
Trend                1.000000   1.000000   1.000000   1.00   1.00  ...   
PredictValue         7.500456  30.570659  49.097035  10.64  30.75  ...   
Error               -0.029544  -0.429341  -1.012965  -1.12   0.75  ...   
PredictedTrend       0.000000   0.000000   0.000000   0.00   1.00  ...   

                         ZNGA        ZNH   ZOES        ZSAN    ZTO       ZTS  \
DATE                                                                           
2018-01-01 00:00:00  9.500000  21.000000  24.72  220.200000  16.57  31.01000   
2018-01-02 00:00:00  9.050000  20.666700  25.10  221.000000  16.99  31.02000   
2018-01-03 00:00:00  9.240000  20.500000  25.20  224.000000  16.93  31.04000   
2018-01-04 00:00:00  9.470000  20.500000  28.21  221.800000  16.00  31.03000   
2018-01-05 00:00:00  9.470000  20.375300  27.89  221.800000  16.00  32.00000   
...                       ...        ...    ...         ...    ...       ...   
2018-09-19 00:00:00  2.540000   3.958700  34.09   45.600000  15.73  30.36000   
Trend                1.000000   1.000000   1.00    0.000000   1.00   1.00000   
PredictValue         2.607002   3.933278  33.55   46.948589  15.63  30.77699   
Error                0.067002  -0.025422  -0.54    1.348589  -0.10   0.41699   
PredictedTrend       1.000000   1.000000   0.00    0.000000   1.00   1.00000   

                          ZUMZ        ZX   ZYME       ZYNE  
DATE                                                        
2018-01-01 00:00:00  12.435000  5.850000  13.00  16.250000  
2018-01-02 00:00:00  12.255000  6.250000  13.07  19.320000  
2018-01-03 00:00:00  12.050000  6.300000  13.10  24.540000  
2018-01-04 00:00:00  12.125000  6.040000  13.28  35.140000  
2018-01-05 00:00:00  11.750000  6.080000  13.11  29.730000  
...                        ...       ...    ...        ...  
2018-09-19 00:00:00  34.820000  3.460000  11.98  10.500000  
Trend                 1.000000  0.000000   1.00   1.000000  
PredictValue         35.351779  3.505572  11.98   8.790237  
Error                 0.531779  0.045572   0.00  -1.709763  
PredictedTrend        1.000000  1.000000   1.00   0.000000  

[266 rows x 3568 columns]

In [186]:
# set the values for PredictedTrend
for column in close_prices.columns[0:]:
    if (close_prices[column][263] - close_prices[column][260]) >= 0:
        close_prices[column][265] = 1   # 1 = UP
    else:
        close_prices[column][265] = 0   # 2 = Down

In [195]:
###### the accuracy of predicted trend
count = 0
for column in close_prices.columns[0:]:
    if (close_prices[column][-1] == close_prices[column][-4]):
        count = count + 1
print(count/len(close_prices.columns))
# too bad bruhhhhh
# my guessing is even better than this :(
# the good thing is ARIMA is actually for exact prices and the error is not that bad tho...

0.5190582959641256


In [219]:
close_prices = close_prices.transpose()

In [220]:
close_prices.to_csv(r'close_prices_added.csv')

###### merging & cleaning 

In [53]:
# 1. import the close prices 
close = pd.read_csv('close_prices_added.csv')

In [54]:
close.rename(columns = {'Unnamed: 0':'Symbol', '9/18/2018 0:00': 'LastDay', '9/19/2018 0:00': 'TruePrice'}, inplace = True)
close = close.set_index('Symbol')

In [55]:
closes = close[close.columns[~close.columns.str.contains('0:00')]] 

In [56]:
closes

LastDay  TruePrice  Trend  PredictValue     Error  PredictedTrend
Symbol                                                                   
A       28.0462    31.9205      1     29.225400 -2.695100               1
AAC     22.5900    24.4300      1     22.250000 -2.180000               0
AAOI    16.9600    16.8100      0     17.901029  1.091029               1
AAP     17.3033    17.1830      0     17.410343  0.227343               1
AAT     20.4300    20.6900      1     20.705901  0.015901               1
...         ...        ...    ...           ...       ...             ...
ZTS     30.3600    30.3600      1     30.776990  0.416990               1
ZUMZ    34.8200    34.8200      1     35.351779  0.531779               1
ZX       3.4700     3.4600      0      3.505572  0.045572               1
ZYME    11.9800    11.9800      1     11.980000  0.000000               1
ZYNE     9.4300    10.5000      1      8.790237 -1.709763               0

[3568 rows x 6 columns]

In [37]:
# 2. import the original data
ipos = pd.read_csv('IPODataFull.csv', encoding= 'unicode_escape')

In [38]:
ipos.head()

Symbol  DaysBetterThanSP  daysProfit daysProfitGrouped  exactDiffernce  \
0      A               122         249              200+             NaN   
1    AAC               131         262              200+           232.0   
2   AAOI               125         262              200+          6054.0   
3    AAP               128         261              200+             NaN   
4    AAT               123         127         100 - 149           181.0   

   Year  Month  Day  dayOfWeek  closeDay0  ...  usableCEOAge  usableCEOGender  \
0  1999     11   18          3    28.6358  ...         Blank            Blank   
1  2014     10    2          3    18.5000  ...       40 - 49             male   
2  2013      9   26          3     9.9600  ...         Blank            Blank   
3  2001     11   29          3    13.9000  ...         Blank            Blank   
4  2011      1   13          3    21.2500  ...         Blank            Blank   

   usablePresidentAge  usablePresidentGender  FoundingDateGrouped  \
0               Blank                  Blank          1951 - 2000   
1               Blank                  Blank       2011 - present   
2               Blank                  Blank          1951 - 2000   
3               Blank                  Blank          1901 - 1950   
4               Blank                  Blank          2001 - 2010   

   yearDifferenceGrouped  Profitable  Safe  HomeRunDay  HomeRun  
0                Unknown           1     0        77.0        1  
1                Unknown           1     1         NaN        0  
2                Unknown           1     0         NaN        0  
3                Unknown           1     0         NaN        0  
4                Unknown           0     0         NaN        0  

[5 rows x 1664 columns]

In [39]:
# delete all the columns representing prices
ipos = ipos[ipos.columns[~ipos.columns.str.contains('openDay')]] 
ipos = ipos[ipos.columns[~ipos.columns.str.contains('closeDay')]] 
ipos = ipos[ipos.columns[~ipos.columns.str.contains('highDay')]] 
ipos = ipos[ipos.columns[~ipos.columns.str.contains('lowDay')]] 
ipos = ipos[ipos.columns[~ipos.columns.str.contains('volumeDay')]] 

In [44]:
ipos = ipos.set_index('Symbol')

In [52]:
closes

Symbol  LastDay  TruePrice  Trend  PredictValue     Error  PredictedTrend
0         A  28.0462    31.9205      1     29.225400 -2.695100               1
1       AAC  22.5900    24.4300      1     22.250000 -2.180000               0
2      AAOI  16.9600    16.8100      0     17.901029  1.091029               1
3       AAP  17.3033    17.1830      0     17.410343  0.227343               1
4       AAT  20.4300    20.6900      1     20.705901  0.015901               1
...     ...      ...        ...    ...           ...       ...             ...
3563    ZTS  30.3600    30.3600      1     30.776990  0.416990               1
3564   ZUMZ  34.8200    34.8200      1     35.351779  0.531779               1
3565     ZX   3.4700     3.4600      0      3.505572  0.045572               1
3566   ZYME  11.9800    11.9800      1     11.980000  0.000000               1
3567   ZYNE   9.4300    10.5000      1      8.790237 -1.709763               0

[3568 rows x 7 columns]

In [103]:
# attach the info extracted from closes price
data = ipos.merge(closes , left_index=True, right_index=True, copy = False)

In [104]:
# change all 'Unknown' to NaN
data.replace('Unknown',np.nan, inplace = True)

In [105]:
# drop the columns with too many missing values
frac = len(data) * 0.8
data = data.dropna(thresh=frac, axis=1)

In [106]:
# check the # of missing values and unique values
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', -1)

def miss_unique(dataframe):
    unique_count = []
    for x in dataframe.columns:
        unique_count.append([x,len(dataframe[x].unique()),dataframe[x].isnull().sum()])

    return pd.DataFrame(unique_count, columns=["Column","Unique","Missing"]).set_index("Column").T

miss_unique(data)

Column   DaysBetterThanSP  daysProfit  daysProfitGrouped  Year  Month  Day  \
Unique   153               263         5                  22    12     31    
Missing  0                 0           0                  0     0      0     

Column   dayOfWeek  Name  LastSale  MarketCap  Sector  Industry  \
Unique   5          3389  2667      3397       13      132        
Missing  0          0     1         0          707     707        

Column   Summary Quote  ipoDate  CEOAge  CEOName  CEOGender  PresidentName  \
Unique   3506           2128     58      2771     7          2565            
Missing  0              0        682     451      449        643             

Column   PresidentGender  MarketMonthTrend  Market3MonthTrend  \
Unique   7                2033              2033                
Missing  642              0                 0                   

Column   Market6MonthTrend  MarketYearTrend  Profitable  Safe  HomeRun  \
Unique   2033               2033             2           2     2         
Missing  0                  0                0           0     0         

Column   LastDay  TruePrice  Trend  PredictValue  Error  PredictedTrend  
Unique   2677     2674       2      3294          2646   2               
Missing  0        0          0      0             0      0

In [107]:
# check the size of data
len(data)

3568

In [108]:
# delete columns that have too many missing values & unique values (categorical)
data = data.drop(['Name', 'Year','Month', 'Day', 'Sector','Industry',
                 'Summary Quote', 'ipoDate', 'CEOAge', 'CEOName',
                 'CEOGender','PresidentName','PresidentGender'], axis=1)
miss_unique(data)

Column   DaysBetterThanSP  daysProfit  daysProfitGrouped  dayOfWeek  LastSale  \
Unique   153               263         5                  5          2667       
Missing  0                 0           0                  0          1          

Column   MarketCap  MarketMonthTrend  Market3MonthTrend  Market6MonthTrend  \
Unique   3397       2033              2033               2033                
Missing  0          0                 0                  0                   

Column   MarketYearTrend  Profitable  Safe  HomeRun  LastDay  TruePrice  \
Unique   2033             2           2     2        2677     2674        
Missing  0                0           0     0        0        0           

Column   Trend  PredictValue  Error  PredictedTrend  
Unique   2      3294          2646   2               
Missing  0      0             0      0

In [109]:
# drop missing values
data = data.dropna(axis=0)

In [110]:
data = data.drop(['Error','PredictedTrend'], axis = 1)

In [111]:
data.head()

DaysBetterThanSP  daysProfit daysProfitGrouped  dayOfWeek  LastSale  \
Symbol                                                                        
A       122               249         200+              3          68.17      
AAC     131               262         200+              3          11.07      
AAOI    125               262         200+              3          29.97      
AAP     128               261         200+              3          106.45     
AAT     123               127         100 - 149         3          34.00      

           MarketCap  MarketMonthTrend  Market3MonthTrend  Market6MonthTrend  \
Symbol                                                                         
A       2.198323e+10  1.601165          2.352508           2.312974            
AAC     2.707691e+08 -2.452645         -1.194498           0.138536            
AAOI    5.844368e+08  0.761732          0.926398           1.286165            
AAP     7.874971e+09  0.613550          1.153716          -0.128110            
AAT     1.604956e+09  1.692499          1.824305           1.813736            

        MarketYearTrend  Profitable  Safe  HomeRun  LastDay  TruePrice  Trend  \
Symbol                                                                          
A       2.039844         1           0     1        28.0462  31.9205    1       
AAC     0.881839         1           1     0        22.5900  24.4300    1       
AAOI    1.443672         1           0     0        16.9600  16.8100    0       
AAP    -0.745906         1           0     0        17.3033  17.1830    0       
AAT     2.263666         0           0     0        20.4300  20.6900    1       

        PredictValue  
Symbol                
A       29.225400     
AAC     22.250000     
AAOI    17.901029     
AAP     17.410343     
AAT     20.705901

In [112]:
data.tail()

DaysBetterThanSP  daysProfit daysProfitGrouped  dayOfWeek  LastSale  \
Symbol                                                                        
ZTS     115               226         200+              4          84.40      
ZUMZ    139               261         200+              4          24.10      
ZX      102               25          0 - 49            3          1.30       
ZYME    115               19          0 - 49            4          12.05      
ZYNE    104               42          0 - 49            2          10.02      

           MarketCap  MarketMonthTrend  Market3MonthTrend  Market6MonthTrend  \
Symbol                                                                         
ZTS     4.094335e+10  1.830451          1.941604           2.497749            
ZUMZ    6.085133e+08  0.510960         -0.612410          -0.792605            
ZX      6.711250e+07  0.592945          1.166548           1.254664            
ZYME    3.068106e+08  1.516558          1.160791           1.263619            
ZYNE    1.358850e+08  0.173427         -0.064559           0.239617            

        MarketYearTrend  Profitable  Safe  HomeRun  LastDay  TruePrice  Trend  \
Symbol                                                                          
ZTS     2.456595         1           0     0        30.36    30.36      1       
ZUMZ    0.546793         1           1     1        34.82    34.82      1       
ZX      1.485474         0           0     0        3.47     3.46       0       
ZYME    1.739724         0           0     0        11.98    11.98      1       
ZYNE    0.835617         0           0     0        9.43     10.50      1       

        PredictValue  
Symbol                
ZTS     30.776990     
ZUMZ    35.351779     
ZX      3.505572      
ZYME    11.980000     
ZYNE    8.790237

In [85]:
# sefine X and y
y_trend = data['Trend']
X_trend = data.copy()
X_trend = X_trend.drop(['Trend','TruePrice'],axis = 1)

<bound method NDFrame.head of         DaysBetterThanSP  daysProfit daysProfitGrouped  dayOfWeek   LastSale  \
Symbol                                                                         
A       122               249         200+              3          68.1700     
AAC     131               262         200+              3          11.0700     
AAOI    125               262         200+              3          29.9700     
AAP     128               261         200+              3          106.4500    
AAT     123               127         100 - 149         3          34.0000     
AAV     76                1           0 - 49            0          3.1500      
AAWW    96                224         200+              2          64.5000     
AAXJ    125               0           0 - 49            2          77.0100     
ABAC    103               72          50 - 99           1          2.5200      
ABB     59                255         200+              4          23.0100     
ABBV    13

In [92]:
# make daysProfitGrouped categorical variable
le = LabelEncoder()
X_trend['daysProfitGrouped'] = le.fit_transform(X_trend['daysProfitGrouped'])

In [94]:
X_trend = pd.get_dummies(X_trend, columns = ['daysProfitGrouped'])

In [101]:
# for MarketMonthTrend negative 0, positive 1

for column in X_trend.columns[0:]:
    if 'MonthTrend' in column or 'YearTrend' in column:
        for i in range(0,len(data[column])):
            if X_trend[column].iloc[i] <= 0:
                X_trend[column].iloc[i] = 0
            else:
                X_trend[column].iloc[i] = 1


In [102]:
X_trend.head()

DaysBetterThanSP  daysProfit  dayOfWeek  LastSale     MarketCap  \
Symbol                                                                    
A       122               249         3          68.17     2.198323e+10   
AAC     131               262         3          11.07     2.707691e+08   
AAOI    125               262         3          29.97     5.844368e+08   
AAP     128               261         3          106.45    7.874971e+09   
AAT     123               127         3          34.00     1.604956e+09   

        MarketMonthTrend  Market3MonthTrend  Market6MonthTrend  \
Symbol                                                           
A       1.0               1.0                1.0                 
AAC     0.0               0.0                1.0                 
AAOI    1.0               1.0                1.0                 
AAP     1.0               1.0                0.0                 
AAT     1.0               1.0                1.0                 

        MarketYearTrend  Profitable  Safe  HomeRun  LastDay  PredictValue  \
Symbol                                                                      
A       1.0              1           0     1        28.0462  29.225400      
AAC     1.0              1           1     0        22.5900  22.250000      
AAOI    1.0              1           0     0        16.9600  17.901029      
AAP     0.0              1           0     0        17.3033  17.410343      
AAT     1.0              0           0     0        20.4300  20.705901      

        daysProfitGrouped_0  daysProfitGrouped_1  daysProfitGrouped_2  \
Symbol                                                                  
A       0                    0                    0                     
AAC     0                    0                    0                     
AAOI    0                    0                    0                     
AAP     0                    0                    0                     
AAT     0                    1                    0                     

        daysProfitGrouped_3  daysProfitGrouped_4  
Symbol                                            
A       1                    0                    
AAC     1                    0                    
AAOI    1                    0                    
AAP     1                    0                    
AAT     0                    0

In [114]:
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
from sklearn.neighbors import KNeighborsClassifier
from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel

In [152]:
#split training and testing data
X_trend_train, X_trend_test, y_trend_train, y_trend_test = train_test_split(X_trend, y_trend, 
                                        test_size=0.2, random_state=42)

### RandomForestClassifier

In [153]:
rf_basic = RandomForestClassifier()
rf_basic.fit(X_trend_train, y_trend_train)
y_predict = rf_basic.predict(X_trend_test)
print('rf:',accuracy_score(y_trend_test, y_predict))

rf: 0.6862745098039216


In [154]:
# noremalization
# normalize the data 
from sklearn import preprocessing
X_trend_norm = preprocessing.normalize(X_trend)

In [155]:
X_trend_train_n, X_trend_test_n, y_trend_train_n, y_trend_test_n = train_test_split(X_trend_norm, y_trend, 
                                        test_size=0.2, random_state=42)
rf_basic.fit(X_trend_train_n, y_trend_train_n)
y_predict = rf_basic.predict(X_trend_test_n)
print('rf:',accuracy_score(y_trend_test_n, y_predict))

rf: 0.6918767507002801


In [127]:
lgbm_basic = LGBMClassifier()
lgbm_basic.fit(X_trend_train_n, y_trend_train_n)
y_predict = lgbm_basic.predict(X_trend_test_n)
print('lgbm: ',accuracy_score(y_trend_test_n, y_predict))

lgbm:  0.6834733893557423


In [133]:
for feature in zip(X_trend.columns, rf_basic.feature_importances_):
    print(feature)

('DaysBetterThanSP', 0.13153246491528886)
('daysProfit', 0.09885172986659437)
('dayOfWeek', 0.17253258909575722)
('LastSale', 0.12313302199765519)
('MarketCap', 0.12327928076150044)
('MarketMonthTrend', 0.016585855341879684)
('Market3MonthTrend', 0.015051519306175149)
('Market6MonthTrend', 0.011505961323989422)
('MarketYearTrend', 0.01270419208914187)
('Profitable', 0.006939960681012419)
('Safe', 0.008671284798188841)
('HomeRun', 0.00782302590013938)
('LastDay', 0.11761737134783552)
('PredictValue', 0.11998306144821702)
('daysProfitGrouped_0', 0.006668350266329233)
('daysProfitGrouped_1', 0.007519196571456324)
('daysProfitGrouped_2', 0.006539136666726004)
('daysProfitGrouped_3', 0.006938938298617321)
('daysProfitGrouped_4', 0.006123059323495617)


In [156]:
# drop the variables which are selected as less important
X_f = X_trend[['DaysBetterThanSP','dayOfWeek','LastSale',
                     'MarketCap','LastDay','PredictValue']]

In [157]:
# normalization
X_f = preprocessing.normalize(X_f)

In [170]:
from sklearn.svm import SVC

X_trend_train_f, X_trend_test_f, y_trend_train_f, y_trend_test_f = train_test_split(X_f, y_trend, 
                                        test_size=0.2, random_state=42)
svc = SVC()
svc.fit(X_trend_train_f, y_trend_train_f)
y_predict = svc.predict(X_trend_test_f)
print('svc:',accuracy_score(y_trend_test_f, y_predict))

svc: 0.6918767507002801


In [160]:
### PCA & grad search for random forest
from sklearn import decomposition
from sklearn import pipeline
from sklearn.model_selection import GridSearchCV

rf = RandomForestClassifier()

# Create a pca object
pca = decomposition.PCA()

# tranform the data with PCA.
# Third, train a Decision Tree Classifier on the data.
pipe = pipeline.Pipeline(steps=[('pca', pca),
                           ('rf', rf)])

    
# Create lists of parameter for lgbmclassifier

    
params = {'rf__max_depth': [60,70,80],
         'rf__min_samples_leaf': [1,2, 4,8,12],
         'rf__min_samples_split': [2, 5, 10],
         'rf__bootstrap': [True, False]}

rf_pca = GridSearchCV(estimator=pipe , param_grid=params, cv = 5)

In [161]:
rf_pca.fit(X_trend_train_n, y_trend_train_n)
y_predict = rf_pca.predict(X_trend_test_n)
accuracy_score(y_trend_test_n, y_predict)

0.6918767507002801

In [171]:
### grid search for svc
from sklearn.model_selection import GridSearchCV
svc = SVC()
param = {
    'C': [0.1,1,10],
    'gamma': [0.1,1,10,100],
    'kernel': ['linear','rbf','poly']
}
grid_search = GridSearchCV(estimator = svc, param_grid = param, 
                          cv = 5)

In [172]:
svc_grid = grid_search.fit(X_trend_train_f, y_trend_train_f)

In [173]:
y_predict = svc_grid.predict(X_trend_test_f)
accuracy_score(y_trend_test_f, y_predict)

0.6918767507002801